# HuggingFace challenge - Debugger notebook
Run this notebook to verify your libraries versions, check GPU config and run a quick training

In [1]:
# %%capture
# !pip install https://github.com/kpu/kenlm/archive/master.zip pyctcdecode
# !pip install datasets==1.18.3
# !pip install git+https://github.com/huggingface/transformers.git
# !pip install huggingface_hub==0.1
# !pip install torchaudio==0.10.0+cu113 -f https://download.pytorch.org/whl/cu113/torch_stable.html
# !pip install jiwer
# !pip install -U git+https://github.com/huggingface/transformers.git

In [2]:
# !pip install -U git+https://github.com/huggingface/transformers.git

  Cloning https://github.com/huggingface/transformers.git to /tmp/pip-req-build-i45amciw
  Running command git clone -q https://github.com/huggingface/transformers.git /tmp/pip-req-build-i45amciw
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
    Preparing wheel metadata ... done


In [1]:
import platform
import multiprocessing

import torch
import transformers
import datasets

import soundfile

## Print main infos

In [2]:
print(f"Platform: {platform.platform()}")
print(f"CPU cores: {multiprocessing.cpu_count()}")

print(f"Python version: {platform.python_version()}")

print(f"PyTorch version: {torch.__version__}")
print(f"GPU is visible: {torch.cuda.is_available()}")

print(f"Transformers version: {transformers.__version__}")
print(f"Datasets version: {datasets.__version__}")

print(f"soundfile version: {soundfile.__version__}")

Platform: Linux-5.11.0-37-generic-x86_64-with-glibc2.10
CPU cores: 60
Python version: 3.8.8
PyTorch version: 1.10.1+cu102
GPU is visible: True
Transformers version: 4.16.0.dev0
Datasets version: 1.18.3
soundfile version: 0.10.3


## Check your GPU informations (if any)
If you launched an AI Training job with GPU resources, they should be listed below (Tesla V100s 32GB).
Driver and CUDA version 

In [3]:
!nvidia-smi

Sat Jan 29 03:27:00 2022       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 470.57.02    Driver Version: 470.57.02    CUDA Version: 11.4     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla V100S-PCI...  Off  | 00000000:00:06.0 Off |                    0 |
| N/A   35C    P0    26W / 250W |      4MiB / 32510MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [7]:
from huggingface_hub import notebook_login

notebook_login()

Login successful
Your token has been saved to /root/.huggingface/token
Authenticated through git-crendential store but this isn't the helper defined on your machine.
You will have to re-authenticate when pushing to the Hugging Face Hub. Run the following command in your terminal to set it as the default

git config --global credential.helper store


In [8]:
%%capture
!apt install git-lfs

## Quick training run with a dummy model and data
more information on https://github.com/huggingface/transformers/tree/master/examples/pytorch/speech-recognition

In [12]:
!wget -O run_speech_recognition_ctc.py https://raw.githubusercontent.com/huggingface/transformers/master/examples/pytorch/speech-recognition/run_speech_recognition_ctc.py
# !wget -O run_speech_recognition_ctc.py https://raw.githubusercontent.com/huggingface/transformers/master/examples/research_projects/robust-speech-event/run_speech_recognition_ctc_bnb.py

--2022-01-28 09:12:30--  https://raw.githubusercontent.com/huggingface/transformers/master/examples/research_projects/robust-speech-event/run_speech_recognition_ctc_bnb.py
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.110.133, 185.199.111.133, 185.199.109.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.110.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 31209 (30K) [text/plain]
Saving to: ‘run_speech_recognition_ctc.py’

run_speech_recognit 100%[===================>]  30.48K  --.-KB/s    in 0.001s  

2022-01-28 09:12:30 (21.4 MB/s) - ‘run_speech_recognition_ctc.py’ saved [31209/31209]



In [9]:
# 	--learning_rate="7.5e-5" \
# 84.5

In [9]:
!nvcc --version

nvcc: NVIDIA (R) Cuda compiler driver
Copyright (c) 2005-2020 NVIDIA Corporation
Built on Mon_Oct_12_20:09:46_PDT_2020
Cuda compilation tools, release 11.1, V11.1.105
Build cuda_11.1.TC455_06.29190527_0


In [10]:
!pip install bitsandbytes-cuda111

     |████████████████████████████████| 4.0 MB 4.3 MB/s 


In [20]:
!python run_speech_recognition_ctc.py \
	--dataset_name="mozilla-foundation/common_voice_7_0" \
	--model_name_or_path="facebook/wav2vec2-xls-r-300m" \
	--dataset_config_name="cy" \
	--output_dir="./wav2vec2-large-xls-r-300m-welsh" \
	--overwrite_output_dir \
	--num_train_epochs="50" \
	--per_device_train_batch_size="32" \
	--per_device_eval_batch_size="16" \
	--gradient_accumulation_steps="1" \
	--learning_rate="7e-5" \
	--warmup_steps="3000" \
	--length_column_name="input_length" \
	--evaluation_strategy="steps" \
	--text_column_name="sentence" \
	--chars_to_ignore , ? . ! \- \; \: \" “ % ‘ ” � — ’ … – \' \
	--save_steps="3000" \
	--eval_steps="3000" \
	--logging_steps="100" \
	--layerdrop="0.0" \
	--activation_dropout="0.1" \
	--save_total_limit="2" \
	--freeze_feature_encoder \
	--feat_proj_dropout="0.0" \
	--mask_time_prob="0.75" \
	--mask_time_length="10" \
	--mask_feature_prob="0.25" \
	--mask_feature_length="64" \
	--gradient_checkpointing \
	--use_auth_token \
	--fp16 \
	--group_by_length \
	--do_train --do_eval \
    --push_to_hub > out.log

remove special characters from datasets: 11695ex [00:02, 4262.69ex/s]
remove special characters from datasets: 4850ex [00:01, 4827.87ex/s]
loading configuration file https://huggingface.co/facebook/wav2vec2-xls-r-300m/resolve/main/config.json from cache at /workspace/.cache/huggingface/transformers/dabc27df63e37bd2a7a221c7774e35f36a280fbdf917cf54cadfc7df8c786f6f.a3e4c3c967d9985881e0ae550a5f6f668f897db5ab2e0802f9b97973b15970e6
Model config Wav2Vec2Config {
  "_name_or_path": "facebook/wav2vec2-xls-r-300m",
  "activation_dropout": 0.0,
  "adapter_kernel_size": 3,
  "adapter_stride": 2,
  "add_adapter": false,
  "apply_spec_augment": true,
  "architectures": [
    "Wav2Vec2ForPreTraining"
  ],
  "attention_dropout": 0.1,
  "bos_token_id": 1,
  "classifier_proj_size": 256,
  "codevector_dim": 768,
  "contrastive_logits_temperature": 0.1,
  "conv_bias": true,
  "conv_dim": [
    512,
    512,
    512,
    512,
    512,
    512,
    512
  ],
  "conv_kernel": [
    10,
    3,
    3,
    3,
  

In [ ]:
# !rm -rf wav2vec2-large-xls-r-300m-bashkir

In [ ]:
!ls -ltr

In [ ]:
!df -h

Filesystem      Size  Used Avail Use% Mounted on
overlay         3.5T  1.2T  2.2T  34% /
tmpfs            64M     0   64M   0% /dev
tmpfs            87G     0   87G   0% /sys/fs/cgroup
tmpfs            87G     0   87G   0% /dev/shm
/dev/md0        3.5T  1.2T  2.2T  34% /etc/group
tmpfs            87G   12K   87G   1% /proc/driver/nvidia
/dev/vda1        49G  6.5G   42G  14% /usr/bin/nvidia-smi
udev             87G     0   87G   0% /dev/nvidia0
tmpfs            87G     0   87G   0% /proc/acpi
tmpfs            87G     0   87G   0% /proc/scsi
tmpfs            87G     0   87G   0% /sys/firmware


In [ ]:
# !pip install -U datasets

In [1]:
from datasets import load_dataset, load_metric, Audio

common_voice_train = load_dataset("mozilla-foundation/common_voice_7_0", "cy", use_auth_token=True, split="train+validation")
common_voice_test = load_dataset("mozilla-foundation/common_voice_7_0", "cy", use_auth_token=True, split="test")

print(len(common_voice_train))

0 examples [00:00, ? examples/s]

0 examples [00:00, ? examples/s]

0 examples [00:00, ? examples/s]

0 examples [00:00, ? examples/s]

0 examples [00:00, ? examples/s]

Dataset common_voice downloaded and prepared to /workspace/.cache/huggingface/datasets/mozilla-foundation___common_voice/cy/7.0.0/fe20cac47c166e25b1f096ab661832e3da7cf298ed4a91dcaa1343ad972d175b. Subsequent calls will reuse this data.


Reusing dataset common_voice (/workspace/.cache/huggingface/datasets/mozilla-foundation___common_voice/cy/7.0.0/fe20cac47c166e25b1f096ab661832e3da7cf298ed4a91dcaa1343ad972d175b)


11695


In [2]:
common_voice_train

Dataset({
    features: ['client_id', 'path', 'audio', 'sentence', 'up_votes', 'down_votes', 'age', 'gender', 'accent', 'locale', 'segment'],
    num_rows: 11695
})

In [17]:
len(common_voice_train) * 50 / 32

18273.4375

In [4]:
common_voice_train = common_voice_train.remove_columns(["accent", "age", "client_id", "down_votes", "gender", "locale", "segment", "up_votes"])
common_voice_test = common_voice_test.remove_columns(["accent", "age", "client_id", "down_votes", "gender", "locale", "segment", "up_votes"])

In [5]:
from datasets import ClassLabel
import random
import pandas as pd
from IPython.display import display, HTML

def show_random_elements(dataset, num_examples=10):
    assert num_examples <= len(dataset), "Can't pick more elements than there are in the dataset."
    picks = []
    for _ in range(num_examples):
        pick = random.randint(0, len(dataset)-1)
        while pick in picks:
            pick = random.randint(0, len(dataset)-1)
        picks.append(pick)
    
    df = pd.DataFrame(dataset[picks])
    display(HTML(df.to_html()))

In [6]:
show_random_elements(common_voice_train.remove_columns(["path", "audio"]), num_examples=10)

In [7]:
import re
chars_to_remove_regex = '[\,\?\.\!\-\;\:\"\“\%\‘\”\�\—\’\…\–\']'

def remove_special_characters(batch):
    batch["sentence"] = re.sub(chars_to_remove_regex, '', batch["sentence"]).lower()
    return batch

In [8]:
common_voice_train = common_voice_train.map(remove_special_characters)
common_voice_test = common_voice_test.map(remove_special_characters)

0ex [00:00, ?ex/s]

0ex [00:00, ?ex/s]

In [9]:
# start_with_ar = common_voice_train.filter(lambda example: "⅛" in example['sentence'])
# start_with_ar[0]

In [10]:
# start_with_ar

In [11]:
def replace_hatted_characters(batch):
#     batch["sentence"] = re.sub('[â]', 'a', batch["sentence"])
#     batch["sentence"] = re.sub('[î]', 'i', batch["sentence"])
#     batch["sentence"] = re.sub('[ô]', 'o', batch["sentence"])
#     batch["sentence"] = re.sub('[û]', 'u', batch["sentence"])
#     batch["sentence"] = re.sub('&', 'and', batch["sentence"])
    return batch

In [12]:
common_voice_train = common_voice_train.map(replace_hatted_characters)
common_voice_test = common_voice_test.map(replace_hatted_characters)

0ex [00:00, ?ex/s]

0ex [00:00, ?ex/s]

In [13]:
def extract_all_chars(batch):
  all_text = " ".join(batch["sentence"])
  vocab = list(set(all_text))
  return {"vocab": [vocab], "all_text": [all_text]}

In [14]:
vocab_train = common_voice_train.map(extract_all_chars, batched=True, batch_size=-1, keep_in_memory=True, remove_columns=common_voice_train.column_names)
vocab_test = common_voice_test.map(extract_all_chars, batched=True, batch_size=-1, keep_in_memory=True, remove_columns=common_voice_test.column_names)

  0%|          | 0/1 [00:00<?, ?ba/s]

  0%|          | 0/1 [00:00<?, ?ba/s]

In [15]:
vocab_list = list(set(vocab_train["vocab"][0]) | set(vocab_test["vocab"][0]))

In [18]:
vocab_dict = {v: k for k, v in enumerate(sorted(vocab_list))}
vocab_dict

{' ': 0,
 'a': 1,
 'b': 2,
 'c': 3,
 'd': 4,
 'e': 5,
 'f': 6,
 'g': 7,
 'h': 8,
 'i': 9,
 'j': 10,
 'k': 11,
 'l': 12,
 'm': 13,
 'n': 14,
 'o': 15,
 'p': 16,
 'q': 17,
 'r': 18,
 's': 19,
 't': 20,
 'u': 21,
 'v': 22,
 'w': 23,
 'x': 24,
 'y': 25,
 'z': 26,
 '¬': 27,
 'à': 28,
 'á': 29,
 'â': 30,
 'ä': 31,
 'é': 32,
 'ê': 33,
 'ë': 34,
 'î': 35,
 'ï': 36,
 'ñ': 37,
 'ò': 38,
 'ô': 39,
 'ö': 40,
 'û': 41,
 'ÿ': 42,
 'ŵ': 43,
 'ŷ': 44}

In [19]:
vocab_dict["|"] = vocab_dict[" "]
del vocab_dict[" "]

vocab_dict["[UNK]"] = len(vocab_dict)
vocab_dict["[PAD]"] = len(vocab_dict)
print(len(vocab_dict))

import json
with open('./vocab.json', 'w') as vocab_file:
    json.dump(vocab_dict, vocab_file)
    
from transformers import Wav2Vec2CTCTokenizer

tokenizer = Wav2Vec2CTCTokenizer.from_pretrained("./", unk_token="[UNK]", pad_token="[PAD]", word_delimiter_token="|")

repo_name = "wav2vec2-large-xls-r-300m-welsh"

# tokenizer.save_pretrained(repo_name)

tokenizer.push_to_hub(repo_name)

47


file ./config.json not found
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.
/opt/conda/lib/python3.8/site-packages/huggingface_hub/hf_api.py:1001: FutureWarning: `create_repo` now takes `token` as an optional positional argument. Be sure to adapt your code!
  warnings.warn(
Cloning https://huggingface.co/infinitejoy/wav2vec2-large-xls-r-300m-welsh into local empty directory.
To https://huggingface.co/infinitejoy/wav2vec2-large-xls-r-300m-welsh
   c6057cb..03ec13a  main -> main



'https://huggingface.co/infinitejoy/wav2vec2-large-xls-r-300m-welsh/commit/03ec13af00e374f3ccee1256ed774c84d572abe4'

In [66]:
!wget -O eval.py https://raw.githubusercontent.com/huggingface/transformers/master/examples/research_projects/robust-speech-event/eval.py
!cp eval.py wav2vec2-large-xls-r-300m-irish
!cp run_speech_recognition_ctc.py wav2vec2-large-xls-r-300m-irish
!ls -ltr wav2vec2-large-xls-r-300m-irish

--2022-01-30 07:10:29--  https://raw.githubusercontent.com/huggingface/transformers/master/examples/research_projects/robust-speech-event/eval.py
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 4738 (4.6K) [text/plain]
Saving to: ‘eval.py’

eval.py             100%[===================>]   4.63K  --.-KB/s    in 0s      

2022-01-30 07:10:29 (16.6 MB/s) - ‘eval.py’ saved [4738/4738]

total 1232584
-rw-r--r-- 1 ovh ovh        300 Jan 30 02:51 vocab.json
-rw-r--r-- 1 ovh ovh        260 Jan 30 02:51 tokenizer_config.json
-rw-r--r-- 1 ovh ovh        309 Jan 30 02:51 special_tokens_map.json
-rw-r--r-- 1 ovh ovh         23 Jan 30 02:51 added_tokens.json
drwxr-xr-x 2 ovh ovh       4096 Jan 30 04:36 checkpoint-500
drwxr-xr-x 2 ovh ovh       4096 Jan 30 06:22 checkpoin

In [21]:
!cd wav2vec2-large-xls-r-300m-welsh;python eval.py \
    --model_id ./ --dataset mozilla-foundation/common_voice_7_0 --config cy --split test --log_outputs

Error: mkl-service + Intel(R) MKL: MKL_THREADING_LAYER=INTEL is incompatible with libgomp-a34b3233.so.1 library.
	Try to import numpy first or set the threading layer accordingly. Set MKL_SERVICE_FORCE_INTEL to force it.


In [68]:
!cd wav2vec2-large-xls-r-300m-irish; python eval.py \
    --model_id ./ --dataset speech-recognition-community-v2/dev_data \
    --config cy --split validation --chunk_length_s 10 --stride_length_s 1

Error: mkl-service + Intel(R) MKL: MKL_THREADING_LAYER=INTEL is incompatible with libgomp-a34b3233.so.1 library.
	Try to import numpy first or set the threading layer accordingly. Set MKL_SERVICE_FORCE_INTEL to force it.


In [ ]:
# from transformers import AutoModelForCTC, Wav2Vec2Processor

# model = AutoModelForCTC.from_pretrained("infinitejoy/wav2vec2-large-xls-r-300m-bashkir")
# processor = Wav2Vec2Processor.from_pretrained("infinitejoy/wav2vec2-large-xls-r-300m-bashkir")



Downloading:   0%|          | 0.00/260 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/574 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/23.0 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/309 [00:00<?, ?B/s]

In [ ]:
# from transformers import AutoModelForCTC, AutoProcessor
# from datasets import load_dataset

# model = AutoModelForCTC.from_pretrained("infinitejoy/wav2vec2-large-xls-r-300m-bashkir")
# processor = AutoProcessor.from_pretrained("infinitejoy/wav2vec2-large-xls-r-300m-bashkir")

# input_values = processor(common_voice_test[0]["audio"]["array"], return_tensors="pt", sampling_rate=16_000).input_values
# # input_values = input_values.to("cuda")

# logits = model(input_values).logits

# assert logits.shape[-1] == 32, logits.shape[-1]

Downloading:   0%|          | 0.00/1.99k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/1.18G [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/212 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/260 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/520 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/23.0 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/309 [00:00<?, ?B/s]

AssertionError: 55

In [1]:
from datasets import Audio, Dataset, load_dataset, load_metric
from transformers import AutoFeatureExtractor, pipeline

dataset = load_dataset("mozilla-foundation/common_voice_7_0", "lv", use_auth_token=True, split="train+validation")

# for testing: only process the first two examples as a test
dataset = dataset.select(range(10))

repo_name = 'infinitejoy/wav2vec2-large-xls-r-300m-latvian'

# load processor
feature_extractor = AutoFeatureExtractor.from_pretrained(repo_name)
# feature_extractor = processor_with_lm.feature_extractor
sampling_rate = feature_extractor.sampling_rate

# resample audio
dataset = dataset.cast_column("audio", Audio(sampling_rate=sampling_rate))

# load eval pipeline
asr = pipeline("automatic-speech-recognition", model=repo_name, feature_extractor=feature_extractor)

# map function to decode audio
def map_to_pred(batch):
    prediction = asr(
        batch["audio"]["array"])

    batch["prediction"] = prediction["text"]
    batch["target"] = batch["sentence"]
    return batch

# run inference on all examples
result = dataset.map(map_to_pred, remove_columns=dataset.column_names)
print(result["prediction"])

print(result['target'])

Reusing dataset common_voice (/workspace/.cache/huggingface/datasets/mozilla-foundation___common_voice/lv/7.0.0/fe20cac47c166e25b1f096ab661832e3da7cf298ed4a91dcaa1343ad972d175b)


Downloading:   0%|          | 0.00/1.99k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/212 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/1.18G [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/293 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/342 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/23.0 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/502 [00:00<?, ?B/s]

  0%|          | 0/10 [00:00<?, ?ex/s]

['nebija nekā tīra ko uzvilkt', 'cēlonis tam ne viens vien', 'visi vilki nav pelēki', 'iedzert aukstu alu būtu labi', 'vai mani mati bija glīti', 'lēnām nesasteidz', 'nerunā man rupjības', 'es vairs nevaru būt tavs elks', 'es atradu mūsu zemes gabalu', 'ko tas sīkais sūds ar mani darītu']
['Nebija nekā tīra, ko uzvilkt?', 'Cēlonis tam - ne viens vien.', 'Visi vilki nav pelēki.', 'Iedzert aukstu alu būtu labi.', 'Vai mani mati bija glīti?', 'Lēnām, nesasteidz.', 'Nerunā man rupjības.', 'Es vairs nevaru būt tavs elks.', 'Es atradu mūsu zemes gabalu.', 'Ko tas sīkais sūds ar mani darītu?']


In [6]:
result[0]["prediction"].replace('[UNK]', '')

"e'ess' qted j'ms' ' ɓ'jhm s' s'm' jtj' jtr'm 'v' ɓ'x'"